In [1]:
pip install filterpy

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 178.0/178.0 kB 4.7 MB/s eta 0:00:0000:01
  Preparing metadata (setup.py) ... done
  Created wheel for filterpy: filename=filterpy-1.4.5-py3-none-any.whl size=110458 sha256=8bef145c6655df9192eb1e48e46e6026ceb9d713046fe1a2af7154b02535ca7b
  Stored in directory: /root/.cache/pip/wheels/0f/0c/ea/218f266af4ad626897562199fbbcba521b8497303200186102
Successfully built filterpy
Note: you may need to restart the kernel to use updated packages.


IN THE CODE BELOW :- 

    1. WE TAKE A CSV FILE OF HISTORICAL AIS DATA AS INPUT (AS REAL TIME FREE SATELLITE AIS DATA IS VERY DIFFUCLT TO FIND )
    
    2. CORRECTING ALL THE AIS DATA BY FOLLOWING THE STEPS GIVEN BELOW :-

            a.USING LANGRANGE INTERPOLATION TO SMOOTH THE ROUTE OF SHIPS FOR    
            
                BETTER MODEL PREDICTION 
            
            b. USING KALMAN FILTER TO CORRECT THE AIS DATA FOR BETTER 
            
                ACCURACY AND PRECISION
            
            c. REMOVING DUPLICATE DATA AND SHIPS WITH LESS THAN 10 HISTORICAL 

                RECORDS

            d. DOING LATITDE AND LONGTUDE CORRECTION USING GEOPY

In [ ]:
import pandas as pd
from geopy.distance import geodesic
import numpy as np
from scipy.interpolate import lagrange, interp1d
from filterpy.kalman import KalmanFilter
from datetime import datetime, timezone
import os

def map_match(ship_data, max_distance_threshold=0.1):
    corrected_data = []
    for i, record in enumerate(ship_data):
        latitude, longitude = record['LAT'], record['LON']
        if i == 0:
            corrected_data.append(record)
            continue
        prev_record = corrected_data[-1]
        prev_latitude, prev_longitude = prev_record['LAT'], prev_record['LON']
        distance = geodesic((prev_latitude, prev_longitude), (latitude, longitude)).kilometers
        if distance > max_distance_threshold:
            corrected_point = correct_coordinate(prev_latitude, prev_longitude, latitude, longitude)
            if corrected_point:
                record['LAT'], record['LON'] = corrected_point
                print(f"Corrected point at index {i}: {corrected_point}")
            else:
                print(f"Skipping correction for point at index {i} due to significant deviation.")
        corrected_data.append(record)
    return corrected_data

def correct_coordinate(prev_lat, prev_lon, cur_lat, cur_lon, correction_factor=0.1):
    prev_point = (prev_lat, prev_lon)
    cur_point = (cur_lat, cur_lon)
    distance = geodesic(prev_point, cur_point).kilometers

    if distance > 0:
        bearing = calculate_initial_compass_bearing(prev_point, cur_point)
        corrected_distance = distance * correction_factor
        new_point = geodesic(kilometers=corrected_distance).destination(prev_point, bearing)
        return new_point.latitude, new_point.longitude
    return None

def calculate_initial_compass_bearing(pointA, pointB):
    if (type(pointA) != tuple) or (type(pointB) != tuple):
        raise TypeError("Only tuples are supported as arguments")
    lat1 = np.radians(pointA[0])
    lat2 = np.radians(pointB[0])
    diffLong = np.radians(pointB[1] - pointA[1])
    x = np.sin(diffLong) * np.cos(lat2)
    y = np.cos(lat1) * np.sin(lat2) - (np.sin(lat1) * np.cos(lat2) * np.cos(diffLong))
    initial_bearing = np.arctan2(x, y)
    initial_bearing = np.degrees(initial_bearing)
    compass_bearing = (initial_bearing + 360) % 360
    return compass_bearing

def delete_invalid_data(ship_data, max_speed_threshold=10, max_turn_angle=15):
    valid_data = []
    for record in ship_data:
        sog = record.get('SOG', None)
        cog = record.get('COG', None)
        if sog is None or cog is None or sog < 0.5 or cog < 0:
            continue  # Skipping invalid data
        valid_data.append(record)
    return valid_data

# def cut_data(ship_data):
#     """
#     Remove duplicate entries from ship data.
#     """
#     cut_data = []
#     for group in ship_data:
#         history = group.get('History', [])
        
#         # Convert history to a DataFrame to easily drop duplicates
#         history_df = pd.DataFrame(history)
        
#         # Remove duplicates based on a subset of columns, e.g., 'BaseDateTime', 'LAT', 'LON'
#         history_df = history_df.drop_duplicates(subset=['BaseDateTime', 'LAT', 'LON'])
        
#         # Convert DataFrame back to list of dictionaries
#         unique_history = history_df.to_dict('records')
        
#         cut_data.append({'MMSI': group['MMSI'], 'History': unique_history})
    
#     return cut_data


def kalman_filter_smoothing(history):
    if len(history) == 0:
        return history  # No data to process

    kf = KalmanFilter(dim_x=4, dim_z=2)
    dt = 1
    kf.F = np.array([[1, dt, 0, 0], [0, 1, 0, 0], [0, 0, 1, dt], [0, 0, 0, 1]])
    kf.H = np.array([[1, 0, 0, 0], [0, 0, 1, 0]])
    kf.P *= 1000.
    kf.Q = np.array([[1, 0, 0, 0], [0, 0.1, 0, 0], [0, 0, 1, 0], [0, 0, 0, 0.1]])
    kf.R = np.array([[5, 0], [0, 5]])
    smoothed_data = []
    first_record = history[0]
    kf.x = np.array([first_record['LAT'], 0, first_record['LON'], 0])
    for record in history:
        measurement = np.array([record['LAT'], record['LON']])
        kf.predict()
        kf.update(measurement)
        record['LAT'], record['LON'] = kf.x[0], kf.x[2]
        smoothed_data.append(record)
    return smoothed_data


import pandas as pd
import numpy as np
from scipy.interpolate import lagrange, interp1d
from datetime import datetime, timezone

def interpolate_trajectory(history, max_time_gap=30):
    if len(history) < 2:
        return history  # Not enough data for interpolation

    # Sort by timestamp to ensure proper interpolation
    history.sort(key=lambda x: x['BaseDateTime'])
    
    interpolated_history = []
    
    for i in range(len(history) - 1):
        interpolated_history.append(history[i])
        current_point = history[i]
        next_point = history[i + 1]
        
        # Calculate the time difference between consecutive points
        time_diff = (next_point['BaseDateTime'] - current_point['BaseDateTime']).total_seconds() / 60
        
        if 0 < time_diff <= max_time_gap:
            num_points_to_interpolate = int(time_diff - 1)
            timestamps = [current_point['BaseDateTime'].timestamp(), next_point['BaseDateTime'].timestamp()]
            latitudes = [current_point['LAT'], next_point['LAT']]
            longitudes = [current_point['LON'], next_point['LON']]
            
            # Linear interpolation
            linear_lat = interp1d(timestamps, latitudes, kind='linear')
            linear_lon = interp1d(timestamps, longitudes, kind='linear')
            
            # Lagrange interpolation
            lagrange_lat = lagrange(timestamps, latitudes)
            lagrange_lon = lagrange(timestamps, longitudes)
            
            # Interpolating intermediate points
            t = np.linspace(timestamps[0], timestamps[1], num=num_points_to_interpolate + 2)
            for j in range(1, num_points_to_interpolate + 1):
                timestamp = t[j]
                
                # Use Lagrange interpolation
                interpolated_lat_lagrange = lagrange_lat(timestamp)
                interpolated_lon_lagrange = lagrange_lon(timestamp)
                
                # Use Linear interpolation
                interpolated_lat_linear = linear_lat(timestamp)
                interpolated_lon_linear = linear_lon(timestamp)
                
                # Optionally: Combine Lagrange and Linear results (e.g., averaging)
                interpolated_lat = (interpolated_lat_lagrange + interpolated_lat_linear) / 2
                interpolated_lon = (interpolated_lon_lagrange + interpolated_lon_linear) / 2
                
                # Convert back to datetime
                interpolated_time = datetime.fromtimestamp(timestamp, tz=timezone.utc)
                
                interpolated_history.append({
                    'BaseDateTime': interpolated_time,
                    'LAT': interpolated_lat,
                    'LON': interpolated_lon
                })
    
    interpolated_history.append(history[-1])
    return interpolated_history

def preprocess_ais_data_from_csv(csv_file_path, output_file_path):
    # Read the CSV file
    df = pd.read_csv(csv_file_path, parse_dates=['BaseDateTime'])
    
    # Remove entries with missing MMSI
    df = df.dropna(subset=['MMSI'])
    
    # Filter ships based on Gulf of Mexico region
    gulf_coords = ((18.0, -94.0), (30.0, -80.0))  # (min_lat, min_lon), (max_lat, max_lon)
    df = df[df.apply(lambda row: gulf_coords[0][0] <= row['LAT'] <= gulf_coords[1][0] and gulf_coords[0][1] <= row['LON'] <= gulf_coords[1][1], axis=1)]
    
    # Sort the data by timestamp (BaseDateTime) in ascending order
    df = df.sort_values(by='BaseDateTime', ascending=True)
    
    # Group the data by Ship MMSI to process each ship separately
    grouped = df.groupby('MMSI')
    
    processed_ships = []

    for mmsi, group in grouped:
        if len(group) < 26:
            print(f"Skipping ship with MMSI {mmsi} due to insufficient data.")
            continue
        
        group = group.sort_values(by='BaseDateTime', ascending=True)
        current_data = group.iloc[-1]
        valid_history = group.iloc[-26:-1]
        valid_history = valid_history.dropna(subset=['SOG', 'COG', 'BaseDateTime'])
        
        if len(valid_history) < 25:
            print(f"Skipping ship with MMSI {mmsi} due to insufficient valid history data.")
            continue
        
        valid_history_records = valid_history.to_dict('records')
        print(f"Initial records for MMSI {mmsi}: {len(valid_history_records)}")

        valid_history_records = map_match(valid_history_records)
        print(f"After map matching for MMSI {mmsi}: {len(valid_history_records)}")
        
        valid_history_records = delete_invalid_data(valid_history_records)
        print(f"After deleting invalid data for MMSI {mmsi}: {len(valid_history_records)}")
        
#         valid_history_records = cut_data(valid_history_records)
#         print(f"After cutting data for MMSI {mmsi}: {len(valid_history_records)}")
        
        valid_history_records = kalman_filter_smoothing(valid_history_records)
        print(f"After Kalman filtering for MMSI {mmsi}: {len(valid_history_records)}")

        interpolated_records = interpolate_trajectory(valid_history_records)
        print(f"After interpolation for MMSI {mmsi}: {len(interpolated_records)}")

        processed_ships.append({'MMSI': mmsi, 'History': valid_history_records})

            # Save the processed data to a CSV file
        processed_df = pd.DataFrame([record for ship in processed_ships for record in ship['History']])
        processed_df.to_csv(output_file_path, index=False)
        print(f"Processed data saved to {output_file_path}")

# Example usage:
preprocess_ais_data_from_csv('/kaggle/input/train-1-dataset/AIS_172604905152866709_363-1726049053911.csv', '/kaggle/working/rishab1.csv')


Skipping ship with MMSI 109010462 due to insufficient data.
Skipping ship with MMSI 187069842 due to insufficient data.
Initial records for MMSI 205042000: 25
Corrected point at index 1: (27.083707649758658, -93.9475739011695)
Corrected point at index 2: (27.084505215083503, -93.94817027812181)
Corrected point at index 3: (27.085576457692422, -93.94896224724829)
Corrected point at index 4: (27.086896970023954, -93.94993131246508)
Corrected point at index 5: (27.08843876767795, -93.95105284544586)
Corrected point at index 6: (27.090220745221597, -93.9523375440917)
Corrected point at index 7: (27.092178787842336, -93.95374127090993)
Corrected point at index 8: (27.09429927371601, -93.95525615677445)
Corrected point at index 9: (27.09656593456109, -93.95687113019139)
Corrected point at index 10: (27.0989591312398, -93.95857523310244)
Corrected point at index 11: (27.101456181069036, -93.96035461435324)
Corrected point at index 12: (27.103758213653226, -93.96199663453652)
Corrected point a

THERE WAS A PROBLEM WITH DIRECTLY USING THIS AIS DATA INTO MODEL DUE TO INACCURACIES STILL LEFT . SO WE CAME UP WITH AN IDEA TO USE A GRAPHICAL REPRESENTATION OF SHIP ROUTES. FOR THAT WE FOR THE STEPS:-

1. Although the AIS data have the advantages of fast updates and a very large geographical range, due to their puncture reception problem, they are also characterized by poor data quality and data density in different regions of great difference. These issues are also a great challenge for the renewal and normalization of sea lanes.

2. Therefore, we used the extraction method for road networks for offshore road networks . This method generates a road network from trajectory point data based on the principal graph structure learning and tree linking strategy.
 
3. It does not depend on data pretreatment, and the noise, low sampling rate, and non-uniformity of the density of the data’s distribution can be minimized, allowing the robust extraction of the feature structure of the maritime traffic routes.

4. It was considered that most ships would travel close to the centerlines of the routes (i.e., the centerline of our final generated road map would be consistent with the peak point of the trajectory point), so we could express the geometric topology of the real-world maritime routes approximately in the form of an undirected graph G. 
5. In this study, the structure of the maritime routes was abstracted into the following form:
𝐺0=(𝑉0,𝐸0,𝑊0).......(1)
 where .....
    a. 𝑉0 represents the node of the graph,
    b. 𝐸0 represents the edge of the graph, and
    c. 𝑊0 represents the connection matrix of the graph in Equation (1).
  After inputting a set of trajectory points, we hoped to obtain the best map that could fit the set of trajectory points, namely 𝐺𝑜𝑝𝑡=(𝑉𝑜𝑝𝑡,𝐸𝑜𝑝𝑡,𝑊𝑜𝑝𝑡)
6. Considering that the maritime route is usually a smooth straight line or curve, the optimal main graph should meet the following two conditions: 
    (1) the distance from all the points to the figure shall be as short as possible, and 
    (2) the edges of the graph are straight or rounded, all the edges are as small as possible, and the main graph representing the basic maritime routes shall be as regular as possible. We found that the reversed graph-embedding technology could satisfy the above two conditions to obtain the best main graph.

We use the reverse graph embedding technique below :-

In [ ]:
import pandas as pd
import numpy as np
import networkx as nx
from scipy.spatial.distance import cdist
from scipy.optimize import minimize
from sklearn.preprocessing import normalize

# Load the preprocessed AIS data
csv_file_path = '/kaggle/working/path/to/your/processed_ais_data.csv'
df = pd.read_csv(csv_file_path)

# Select the first 500 ships
imos = df['IMO'].unique()[:5]
df_subset = df[df['IMO'].isin(imos)]

# Function to construct the initial graph from trajectory points
def construct_initial_graph(df):
    G = nx.Graph()
    
    # Add nodes and edges based on trajectory points
    for _, row in df.iterrows():
        G.add_node(row['IMO'], pos=(row['LON'], row['LAT']))
    
    # Example: Add edges based on a simple distance threshold (adjust as needed)
    positions = np.array([G.nodes[n]['pos'] for n in G.nodes])
    distances = cdist(positions, positions)
    threshold = 0.1  # Distance threshold for edge creation (adjust as needed)
    
    for i, node1 in enumerate(G.nodes):
        for j, node2 in enumerate(G.nodes):
            if i < j and distances[i, j] < threshold:
                G.add_edge(node1, node2)
    
    return G

# Function to optimize the graph structure using the given objective function
# Function to optimize the graph structure using the given objective function
def optimize_graph(G, data_points, gamma, sigma, epsilon, max_iter=10):
    def objective(C_flat):
        # Reshape the flattened C array back into a 2D array
        C = C_flat.reshape(-1, 2)
        
        # Compute distances and penalties
        distances = np.linalg.norm(data_points[:, np.newaxis] - C, axis=2)
        P = np.exp(-distances**2 / sigma)
        P = P / P.sum(axis=1, keepdims=True)
        
        W = nx.adjacency_matrix(G).toarray()
        Q = np.sum(W * np.linalg.norm(C[:, np.newaxis] - C, axis=2)**2)
        fitting_term = np.sum(P * np.linalg.norm(data_points[:, np.newaxis] - C, axis=2)**2)
        
        return Q + fitting_term
    
    # Initialize with the positions of the points
    initial_C = np.array([G.nodes[n]['pos'] for n in G.nodes])
    initial_C_flat = initial_C.flatten()  # Flatten the array to 1D
    
    # Run the optimization
    result = minimize(objective, initial_C_flat, method='L-BFGS-B', options={'maxiter': max_iter})
    
    # Reshape the optimized result back into the original 2D shape
    optimized_C = result.x.reshape(initial_C.shape)
    
    # Update node positions
    for i, node in enumerate(G.nodes):
        G.nodes[node]['pos'] = optimized_C[i]
    
    return G


# Function to calculate the membership matrix P and optimize C
# Function to calculate the membership matrix P and optimize C
# Function to calculate the membership matrix P and optimize C with vectorization and batching
def calculate_C_optimization(df, gamma, sigma, epsilon, batch_size=5):
    X = np.array(df[['LON', 'LAT']])
    C = X.copy()

    def compute_P(C):
        distances = cdist(X, C)
        P = np.exp(-distances**2 / sigma)
        P = P /( P.sum(axis=1, keepdims=True)+1e-10)
        return P

    def compute_W(C):
        G = nx.Graph()
        for i, pos in enumerate(C):
            G.add_node(i, pos=pos)
        distances = cdist(C, C)
        for i, node1 in enumerate(G.nodes):
            for j, node2 in enumerate(G.nodes):
                if i < j and distances[i, j] < 0.1:
                    G.add_edge(i, j)
        return nx.adjacency_matrix(G).toarray()

    # Vectorized objective function for optimization
    def objective(C_flat):
        C_reshaped = C_flat.reshape(-1, 2)
        P = compute_P(C_reshaped)
        W_opt = compute_W(C_reshaped)
        
        # Vectorized computation for the objective function
        diff_X_C = np.linalg.norm(X[:, np.newaxis] - C_reshaped, axis=2) ** 2
        fitting_term = np.sum(P * diff_X_C)
        regularization_term = np.sum(W_opt * (np.linalg.norm(C_reshaped[:, np.newaxis] - C_reshaped, axis=2) ** 2))

        return fitting_term + gamma * regularization_term

    # Batch processing
    num_batches = (len(C) + batch_size - 1) // batch_size

    for batch_idx in range(num_batches):
        start_idx = batch_idx * batch_size
        end_idx = min((batch_idx + 1) * batch_size, len(C))
        
        # Optimize the batch of ships
        C_batch = C[start_idx:end_idx]
        C_flat = C_batch.flatten()
        
        result = minimize(objective, C_flat, method='L-BFGS-B')
        C_new_batch = result.x.reshape(C_batch.shape)
        C[start_idx:end_idx] = C_new_batch
    
    W_opt = compute_W(C)
    return C, W_opt


# Main process
# Main process
def main():
    # Process only the first 500 ships
    imos = df['IMO'].unique()[:100]
    df_subset = df[df['IMO'].isin(imos)]
    
    # Construct the initial graph
    G = construct_initial_graph(df_subset)
    
    # Optimize the graph structure
    gamma = 0.1
    sigma = 1.0
    epsilon = 1e-5
    batch_size = 5  # Adjust batch size as needed for performance
    C, W_opt = calculate_C_optimization(df_subset, gamma, sigma, epsilon, batch_size=batch_size)
    
    print("Optimized C:", C)
    print("Optimized Weight Matrix:", W_opt)

# Run the main process
main()



Filetering Spatial attributes  from our corrected CSV file for spatial Model Input and storing it in a CSV file 

In [ ]:
import pandas as pd
import numpy as np
import networkx as nx
from scipy.spatial.distance import cdist
from scipy.optimize import minimize
from sklearn.preprocessing import normalize
from scipy.spatial import cKDTree  # Add this import

# Load the preprocessed AIS data
csv_file_path = '/kaggle/input/processed/processed_ais_data_1.csv'
df = pd.read_csv(csv_file_path)

# Select the first 20 ships (reduced from 500)
imos = df['IMO'].unique()[:100]
df_subset = df[df['IMO'].isin(imos)]

def construct_initial_graph(df):
    G = nx.Graph()
    positions = df[['LON', 'LAT']].values
    for i, row in enumerate(positions):
        G.add_node(df['IMO'].iloc[i], pos=tuple(row))
    
    # Use KDTree for efficient nearest neighbor search
    tree = cKDTree(positions)
    threshold = 0.1
    pairs = tree.query_pairs(r=threshold)
    
    for i, j in pairs:
        G.add_edge(df['IMO'].iloc[i], df['IMO'].iloc[j])
    
    return G

def optimize_graph(G, data_points, gamma, sigma, epsilon, max_iter=10):
    def objective(C_flat):
        C = C_flat.reshape(-1, 2)
        distances = cdist(data_points, C)
        P = np.exp(-distances**2 / sigma)
        P /= P.sum(axis=1, keepdims=True)
        
        W = nx.adjacency_matrix(G).toarray()
        Q = np.sum(W * cdist(C, C)**2)
        fitting_term = np.sum(P * cdist(data_points, C)**2)
        
        return Q + fitting_term
    
    initial_C = np.array([G.nodes[n]['pos'] for n in G.nodes])
    result = minimize(objective, initial_C.flatten(), method='L-BFGS-B', options={'maxiter': max_iter})
    
    optimized_C = result.x.reshape(initial_C.shape)
    for i, node in enumerate(G.nodes):
        G.nodes[node]['pos'] = optimized_C[i]
    
    return G

def calculate_C_optimization(df, gamma, sigma, epsilon, batch_size=5):
    X = df[['LON', 'LAT']].values
    C = X.copy()

    def compute_P(C):
        distances = cdist(X, C)
        P = np.exp(-distances**2 / sigma)
        P /= (P.sum(axis=1, keepdims=True) + 1e-10)
        return P

    def compute_W(C):
        G = nx.Graph()
        for i, pos in enumerate(C):
            G.add_node(i, pos=pos)
        tree = cKDTree(C)
        pairs = tree.query_pairs(r=0.1)
        G.add_edges_from(pairs)
        return nx.adjacency_matrix(G).toarray()

    def objective(C_flat):
        C_reshaped = C_flat.reshape(-1, 2)
        P = compute_P(C_reshaped)
        W_opt = compute_W(C_reshaped)
        
        diff_X_C = cdist(X, C_reshaped)**2
        fitting_term = np.sum(P * diff_X_C)
        regularization_term = np.sum(W_opt * cdist(C_reshaped, C_reshaped)**2)

        return fitting_term + gamma * regularization_term

    num_batches = (len(C) + batch_size - 1) // batch_size

    for batch_idx in range(num_batches):
        start_idx = batch_idx * batch_size
        end_idx = min((batch_idx + 1) * batch_size, len(C))
        
        C_batch = C[start_idx:end_idx]
        result = minimize(objective, C_batch.flatten(), method='L-BFGS-B')
        C[start_idx:end_idx] = result.x.reshape(C_batch.shape)
    
    W_opt = compute_W(C)
    return C, W_opt

def topology_correction(G):
    dangling_nodes = [node for node in G if G.degree(node) == 1]
    G.remove_nodes_from(dangling_nodes)
    
    components = list(nx.connected_components(G))
    
    if len(components) > 1:
        for i in range(1, len(components)):
            component_1 = list(components[i - 1])
            component_2 = list(components[i])
            
            pos1 = np.array([G.nodes[n]['pos'] for n in component_1])
            pos2 = np.array([G.nodes[n]['pos'] for n in component_2])
            
            distances = cdist(pos1, pos2)
            min_idx = np.unravel_index(distances.argmin(), distances.shape)
            
            G.add_edge(component_1[min_idx[0]], component_2[min_idx[1]])
    
    return G

def save_corrected_data(df, G_corrected, output_file_path):
    unique_imo = df['IMO'].unique()[:100]
    df_filtered = df[df['IMO'].isin(unique_imo)]
    
    df_filtered['Original_LON'] = df_filtered['LON']
    df_filtered['Original_LAT'] = df_filtered['LAT']
    
    corrected_positions = {
        imo: G_corrected.nodes[imo]['pos'] for imo in unique_imo if imo in G_corrected.nodes
    }
    
    corrected_df = pd.DataFrame.from_dict(corrected_positions, orient='index', columns=['Corrected_LON', 'Corrected_LAT'])
    corrected_df.reset_index(inplace=True)
    corrected_df.rename(columns={'index': 'IMO'}, inplace=True)
    
    df_corrected = df_filtered[['IMO', 'Original_LON', 'Original_LAT']].drop_duplicates().reset_index(drop=True)
    df_corrected = df_corrected.merge(corrected_df, on='IMO', how='left')
    
    df_corrected.to_csv(output_file_path, index=False)

def main():
    imos = df['IMO'].unique()[:100]
    df_subset = df[df['IMO'].isin(imos)]
    
    G = construct_initial_graph(df_subset)
    
    gamma = 0.1
    sigma = 1.0
    epsilon = 1e-5
    batch_size = 10
    C, W_opt = calculate_C_optimization(df_subset, gamma, sigma, epsilon, batch_size=batch_size)
    
    G_corrected = topology_correction(G)
    
    output_file_path = '/kaggle/working/corrected_trajectory_data_ok_2.csv'
    save_corrected_data(df_subset, G_corrected, output_file_path)
    
    print("Optimization completed.")
    print(f"Data saved to {output_file_path}")

if __name__ == "__main__":
    main()